# Computation of global mean SST

In this example, we illustrate possible bad choices of chunk when computing horizontal mean SST time-series and time-average SST.

# Extraction of data

First, the SST data is extracted, as well as the cell surfaces.

In [ ]:
from dask.diagnostics import Profiler, ResourceProfiler, CacheProfiler, visualize
import xarray as xr
import matplotlib.pyplot as plt

In [ ]:
data = xr.open_dataset('data/surface_thetao.nc')
data = data.isel(olevel=0)

In [ ]:
mesh = xr.open_dataset('data/mesh_mask_eORCA1_v2.2.nc')
mesh = mesh.isel(z=0, t=0)

In [ ]:
surface = mesh['e2t'] * mesh['e1t']
surface

## Bad choice of chunks

First, let's make a try by divinding our dataset into tiles:

In [ ]:
chunk = {'x': 150, 'y':100}
thetao = data['thetao'].chunk(chunk)
thetao

The surface array is also decomposed into the same chunks

In [ ]:
surfbis = surface.chunk(chunk)
surfbis

Now, the mean time-series is computing by weighting using the cell surface:

In [ ]:
tmean = (thetao * surfbis).sum(dim=['x', 'y']) / surfbis.sum(dim=['x', 'y'])

In [ ]:
%%time
with Profiler() as prof, ResourceProfiler(dt=0.25) as rprof, CacheProfiler() as cprof:
    tmean.compute()

In [ ]:
visualize([prof, rprof, cprof], show=False)

In [ ]:
tmean.data.visualize()

In [ ]:
l = tmean.plot()

Now, the time-average map is computed:

In [ ]:
time_mean = thetao.mean(dim='time_counter')

In [ ]:
%%time
with Profiler() as prof, ResourceProfiler(dt=0.25) as rprof, CacheProfiler() as cprof:
    time_mean.compute()

In [ ]:
visualize([prof, rprof, cprof], show=False)

In [ ]:
time_mean.data.visualize()

In [ ]:
l = time_mean.plot(robust=True, cmap=plt.cm.jet)

## Better choice of chunks

The performance in the above are disappointing. This this due to a bad chunking choice. If the SST is now chunked along the time only.

In [ ]:
chunk = {'time_counter': 70}
thetao = data['thetao'].chunk(chunk)
thetao

In [ ]:
tmean = (thetao * surface).sum(dim=['x', 'y']) / surface.sum(dim=['x', 'y'])

In [ ]:
%%time
with Profiler() as prof, ResourceProfiler(dt=0.25) as rprof, CacheProfiler() as cprof:
    tmean.compute()

In [ ]:
visualize([prof, rprof, cprof], show=False)

In [ ]:
tmean.data.visualize()

In [ ]:
l = tmean.plot()

In [ ]:
time_mean = thetao.mean(dim='time_counter')

In [ ]:
%%time
with Profiler() as prof, ResourceProfiler(dt=0.25) as rprof, CacheProfiler() as cprof:
    time_mean.compute()

In [ ]:
visualize([prof, rprof, cprof], show=False)

In [ ]:
time_mean.data.visualize()

In [ ]:
l = time_mean.plot(robust=True, cmap=plt.cm.jet)